In [11]:
import cv2
import numpy as np 

In [12]:
glasses=cv2.imread('Train/glasses.png',cv2.IMREAD_UNCHANGED)
mustache=cv2.imread('Train/mustache.png',cv2.IMREAD_UNCHANGED)

In [13]:
glassesCasc=cv2.CascadeClassifier('Train/third-party/frontalEyes35x16.xml')
noseCasc=cv2.CascadeClassifier('Train/third-party/Nose18x15.xml')

In [14]:
cap=cv2.VideoCapture(0)

In [15]:
while True:
    ret,frame=cap.read()
    gray=cv2.cvtColor(frame,cv2.COLOR_BGR2GRAY)
    eyes = glassesCasc.detectMultiScale(gray, 1.5, 5, 0)
    for (x, y, w, h) in eyes:
        glasses_resized = cv2.resize(glasses, (w, h))
        alpha_channel = glasses_resized[:, :, 3] / 255.0
        
        # Create a mask for the glasses
        glasses_mask = np.zeros_like(glasses_resized[:, :, 3])
        
        # Copy alpha channel to mask and apply threshold
        glasses_mask[glasses_resized[:, :, 3] > 0] = 255
        
        # Overlay the glasses using the mask
        for c in range(0, 3):
            frame[y:y+h, x:x+w, c] = (1 - alpha_channel) * frame[y:y+h, x:x+w, c] + alpha_channel * glasses_resized[:, :, c]

    nose=noseCasc.detectMultiScale(gray,1.3,5,0)
    for (x, y, w, h) in nose:
        mustache_resized = cv2.resize(mustache, (w, h))
        alpha_channel = mustache_resized[:, :, 3] / 255.0
        
        mustache_mask = np.zeros_like(mustache_resized[:, :, 3])
        
        # Copy alpha channel to mask and apply threshold
        mustache_mask[mustache_resized[:, :, 3] > 0] = 255

        for c in range(0, 3):
            frame[y:y+h, x:x+w, c] = (1 - alpha_channel) * frame[y:y+h, x:x+w, c] + alpha_channel * mustache_resized[:, :, c]

    cv2.imshow('Webcam Feed', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()